# Tableau Data Set
- need special data set for tableau dashboard
- will need to intergrate the long/lat we did prior
- 2 tabs will be used for interactive EDA and visualization
- 1 tab will be dedicated for prediction analysis

In [56]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.ensemble import VotingRegressor
from sklearn.linear_model import LinearRegression, Ridge, Lasso, ElasticNet
from sklearn.preprocessing import StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split, GridSearchCV, KFold
from data_preprocessing_final2 import *

In [ ]:
#set columns
pd.set_option("display.max_columns",None)

#set rows
pd.set_option("display.max_rows",None)

### Read our 2 data files we'll use to combine the long/lat and the address

In [57]:
# read our original data file
df = pd.read_csv('./data/Ames_Housing_Price_Data.csv', index_col=0)

# read the map file
map_df = pd.read_csv('./data/housinglatlong.csv', index_col=0)

### Cleaning the main housing data file
- using our data_preprocessing function we created

In [58]:
cleaning(df)

PID  SalePrice  MSSubClass MSZoning  LotFrontage  LotArea  \
1      909176150     126000          30       RL    68.516053     7890   
2      905476230     139500         120       RL    42.000000     4235   
3      911128020     124900          30  C (all)    60.000000     6060   
4      535377150     114000          70       RL    80.000000     8146   
5      534177230     227000          60       RL    70.000000     8400   
6      908128060     198500          85       RL    64.000000     7301   
7      902135020      93000          20       RM    60.000000     6000   
8      528228540     187687          20       RL    53.000000     3710   
9      923426010     137500          20       RL    74.000000    12395   
10     908186050     140000         180       RM    35.000000     3675   
11     528186170     219500         120       RL    48.000000     6240   
12     923426070     136000          60       RL    63.000000    10475   
13     902204080      80000          30       RM    62.000000     7404   
14     535105100     159000          20       RL    68.516053     9500   
15     907405020     214000          20       RL    70.000000     9135   
16     531382110     163000          60       RL    50.000000     8480   
17     906380120     203000          20       RL    68.000000     8814   
18     909101060      67000          30       RL    45.000000     8248   
19     534152050     205000          20       RL    68.516053    10603   
20     923252075     131250          80       RL    62.000000     7706   
21     531376060     181000          20       RL    65.000000     7441   
22     902201120     115000          20       RM    50.000000     6000   
23     923228080      98000         160       RM    21.000000     1477   
24     902326030     265979          70       RM    65.000000    11700   
25     527451330     105500         160       RM    21.000000     1680   
26     528218100     168165          60       RL    58.000000    13204   
27     916386140     201000          20       RL    73.000000     8925   
28     533221090     177500         160       FV    68.516053     2117   
29     534128010     200000          60       RL    68.516053    10382   
30     528106110     450000          20       RL   105.000000    15431   
31     902206260      91300          30       RM    50.000000     5784   
32     528222090     173500          20       RL    64.000000     7697   
33     528218150     199500          20       RL   100.000000    18494   
34     903400180     207000          50       RL    64.000000    13053   
35     535453210     155000          20       RL    70.000000     7931   
36     916386010     220000          20       RL    88.000000    11896   
37     907181090     196000          60       RL    68.000000     9272   
38     902206020      61500          30       RM    52.000000     7830   
39     527327050     195000          60       RL    68.516053    12046   
40     527455250     129250          20       RL    65.000000     7150   
41     528326110     291000          60       RL    68.516053    11000   
42     914452190     134000          20       RL    71.000000     9187   
43     535425060     186000          20       RL    76.000000    11355   
44     532376250     133500          20       RL    68.516053     8638   
45     535379110     148000          70       RL    60.000000    10800   
46     528118010     325300          60       RL   101.000000    14215   
47     528235160     215000          60       RL    59.000000    11796   
48     905478030     131000          50       RL    60.000000    11409   
49     902106130     109500          30       RM    56.000000     4485   
50     902102080     110000          50       RM    60.000000    10440   
51     909176170     150000          90       RL    60.000000    10890   
52     533206070     193800         120       FV    32.000000     3784   
53     527302020     178000          80       RL    78.000000    12090   
54     907414060 

### Will merge on PID
- Take "Coordinates", "Lat", "Lon" from the map_df
- Merge into the housing data

In [28]:
map_df

SalePrice        PID                        Address  \
0        126000  909176150      436 HAYWARD AVE Ames Iowa   
1        139500  905476230         3416 WEST ST Ames Iowa   
3        124900  911128020         320 S 2ND ST Ames Iowa   
4        114000  535377150     1524 DOUGLAS AVE Ames Iowa   
5        227000  534177230    2304 FILLMORE AVE Ames Iowa   
...         ...        ...                            ...   
2598     121000  903205040   1021 RIDGEWOOD AVE Ames Iowa   
2599     139600  905402060        3619 MARY CIR Ames Iowa   
2600     145000  909275030  2140 SUNSET DR 2142 Ames Iowa   
2601     217500  907192040    5319 CLEMENS BLVD Ames Iowa   
2602     215000  906223180      1025 VERMONT CT Ames Iowa   

                                  Coordinates        Lat        Lon  
0        436 Hayward Ave, Ames, IA 50014, USA  42.017780 -93.651452  
1           3416 West St, Ames, IA 50014, USA  42.024697 -93.664186  
3           320 S 2nd St, Ames, IA 50010, USA  42.021389 -93.614855  
4       1524 Douglas Ave, Ames, IA 50010, USA  42.038070 -93.612065  
5      2304 Fillmore Ave, Ames, IA 50010, USA  42.044900 -93.631893  
...                                       ...        ...        ...  
2598  1021 Ridgewood Ave, Ames, IA 50010, USA  42.031937 -93.626510  
2599       3619 Mary Cir, Ames, IA 50014, USA  42.027798 -93.666899  
2600      2140 Sunset Dr, Ames, IA 50014, USA  42.019944 -93.643206  
2601   5319 Clemens Blvd, Ames, IA 50014, USA  42.016826 -93.690382  
2602     1025 Vermont Ct, Ames, IA 50014, USA  42.031651 -93.682452  

[2558 rows x 6 columns]

In [59]:
# create a subset of the columns we want to merge
map_df = map_df[['PID', 'Coordinates','Lat','Lon']]

# now merge on housing by PID and MapRefNo
df = df.merge(map_df, how ='left', on='PID')

In [60]:
## let's check our new merged dataframe to make sure it worked
df.columns

Index(['PID', 'SalePrice', 'MSSubClass', 'MSZoning', 'LotFrontage', 'LotArea',
       'LotShape', 'LandContour', 'LotConfig', 'LandSlope', 'Neighborhood',
       'Condition1', 'BldgType', 'HouseStyle', 'OverallQual', 'OverallCond',
       'YearBuilt', 'YearRemodAdd', 'RoofStyle', 'Exterior1st', 'Exterior2nd',
       'MasVnrType', 'MasVnrArea', 'ExterQual', 'ExterCond', 'Foundation',
       'BsmtQual', 'BsmtCond', 'BsmtExposure', 'BsmtFinType1', 'BsmtFinType2',
       'HeatingQC', 'CentralAir', 'BedroomAbvGr', 'KitchenQual',
       'TotRmsAbvGrd', 'Functional', 'Fireplaces', 'FireplaceQu', 'GarageType',
       'GarageYrBlt', 'GarageFinish', 'GarageArea', 'GarageQual', 'PavedDrive',
       'WoodDeckSF', 'OpenPorchSF', 'EnclosedPorch', '3SsnPorch',
       'ScreenPorch', 'Fence', 'MoSold', 'YrSold', 'SaleCondition',
       'Bsmt_Unfin_Ratio', 'TotalLivArea', 'Coordinates', 'Lat', 'Lon'],
      dtype='object')

### Checking & Removing Duplicates

In [63]:
# checking for duplicate PIDs
df.PID.duplicated().sum()

1

In [64]:
#locate the row and find the PID
duplicateRowsDF = df[df.duplicated()]
print("Duplicate Rows except first occurence based on all columns are:")
print(duplicateRowsDF)

Duplicate Rows except first occurence based on all columns are:
            PID  SalePrice  MSSubClass MSZoning  LotFrontage  LotArea  \
1817  909276070     194000          50       RL         80.0    12400   

     LotShape LandContour LotConfig LandSlope Neighborhood Condition1  \
1817      Reg         HLS    Inside       Mod      Crawfor       Norm   

     BldgType HouseStyle  OverallQual  OverallCond  YearBuilt  YearRemodAdd  \
1817     1Fam     1.5Fin            5            6       1940          1950   

     RoofStyle Exterior1st Exterior2nd MasVnrType  MasVnrArea ExterQual  \
1817     Gable     Wd Sdng     Wd Sdng       None         0.0        TA   

     ExterCond Foundation BsmtQual BsmtCond BsmtExposure BsmtFinType1  \
1817        TA     CBlock       Gd       TA           Mn          BLQ   

     BsmtFinType2 HeatingQC CentralAir  BedroomAbvGr KitchenQual  \
1817          Unf        TA          Y             2          TA   

      TotRmsAbvGrd Functional  Fireplaces Firepl

In [65]:
# check PID = 909276070
df[df.PID == 909276070]

# both from 2006, can remove

PID  SalePrice  MSSubClass MSZoning  LotFrontage  LotArea  \
1816  909276070     194000          50       RL         80.0    12400   
1817  909276070     194000          50       RL         80.0    12400   

     LotShape LandContour LotConfig LandSlope Neighborhood Condition1  \
1816      Reg         HLS    Inside       Mod      Crawfor       Norm   
1817      Reg         HLS    Inside       Mod      Crawfor       Norm   

     BldgType HouseStyle  OverallQual  OverallCond  YearBuilt  YearRemodAdd  \
1816     1Fam     1.5Fin            5            6       1940          1950   
1817     1Fam     1.5Fin            5            6       1940          1950   

     RoofStyle Exterior1st Exterior2nd MasVnrType  MasVnrArea ExterQual  \
1816     Gable     Wd Sdng     Wd Sdng       None         0.0        TA   
1817     Gable     Wd Sdng     Wd Sdng       None         0.0        TA   

     ExterCond Foundation BsmtQual BsmtCond BsmtExposure BsmtFinType1  \
1816        TA     CBlock       Gd       TA           Mn          BLQ   
1817        TA     CBlock       Gd       TA           Mn          BLQ   

     BsmtFinType2 HeatingQC CentralAir  BedroomAbvGr KitchenQual  \
1816          Unf        TA          Y             2          TA   
1817          Unf        TA          Y             2          TA   

      TotRmsAbvGrd Functional  Fireplaces FireplaceQu GarageType  GarageYrBlt  \
1816             5        Typ           1          Gd     Attchd       1940.0   
1817             5        Typ           1          Gd     Attchd       1940.0   

     GarageFinish  GarageArea GarageQual PavedDrive  WoodDeckSF  OpenPorchSF  \
1816          Unf       410.0         TA          Y           0            0   
1817          Unf       410.0         TA          Y           0            0   

      EnclosedPorch  3SsnPorch  ScreenPorch     Fence  MoSold  YrSold  \
1816              0          0          113  No_Fence       2    2006   
1817              0          0          113  No_Fence       2    2006   

     SaleCondition  Bsmt_Unfin_Ratio  TotalLivArea  \
1816        Normal          0.331853        2618.0   
1817        Normal          0.331853        2618.0   

                                   Address        Lat        Lon  
1816  2022 Greeley St, Ames, IA 50014, USA  42.019521 -93.640405  
1817  2022 Greeley St, Ames, IA 50014, USA  42.019521 -93.640405

In [66]:
# Removing duplicates
df = df.drop_duplicates(subset='PID', keep='first', ignore_index='True')

### Checking for empty addresses
- Crossed checked with the Ames_Real_Estate_Data (PID is not listed there)
- Because of that, removing these rows
- Will cause issues with our dashboard

In [67]:
## Checking for NA addresses and coordinates
df[df['Coordinates'].isnull()]

PID  SalePrice  MSSubClass MSZoning  LotFrontage  LotArea  \
79    531477050      67500          30       RH    70.000000     9800   
109   916253320     330000         120       RM    68.516053     9763   
404   535300120     176000          80       RL   120.000000    19296   
495   902205010      45000          30       RM    50.000000     5925   
558   902477120      34900          30  C (all)    60.000000     7879   
680   909129100     159434          50       RH    55.000000     4500   
683   916252170     230000         120       RM    68.516053     8239   
895   535426150     113500          20       RL    80.000000     9000   
1088  904101170     134432          50       RL    80.000000    17120   
1346  902401130     143000          70       RM    50.000000     9000   
1516  916477060     279900          60       RL    68.516053    11800   
1578  911175360     108000          50  C (all)    60.000000    11040   
2010  902103150     122600          50       RM    57.000000     9184   
2138  916403040     174000          20       RL    42.000000    10331   
2167  902401120     325000          75       RM    75.000000    13500   
2202  923125030      81500          20  A (agr)   125.000000    31250   
2227  908154040     320000          20       RL    86.000000    13286   
2322  912251110      57625          30  I (all)   109.000000    21780   
2523  905450020     127500          20       RL    73.000000     9855   
2529  902205020      85000          50       RM    50.000000     5925   

     LotShape LandContour LotConfig LandSlope Neighborhood Condition1  \
79        Reg         Lvl    Corner       Gtl      SawyerW      Feedr   
109        IR         Lvl    Inside       Gtl      GrnHill       Norm   
404       Reg         Lvl    Corner       Gtl        NAmes     Artery   
495       Reg         Lvl    Corner       Gtl      OldTown       Norm   
558       Reg         Lvl    Inside       Gtl       IDOTRR       Norm   
680        IR         Bnk    Inside       Gtl        SWISU       Norm   
683        IR         Lvl    Inside       Gtl      GrnHill       Norm   
895        IR         HLS    Inside       Mod        NAmes       Norm   
1088      Reg         Lvl    Inside       Gtl      ClearCr      Feedr   
1346      Reg         Lvl    Inside       Gtl      OldTown     Artery   
1516       IR         Lvl    Inside       Gtl       Timber       Norm   
1578      Reg         Low    Inside       Mod       IDOTRR       Norm   
2010      Reg         Lvl    Inside       Gtl      OldTown     Artery   
2138      Reg         Lvl   CulDSac       Gtl       Timber       Norm   
2167      Reg         Lvl    Inside       Gtl      OldTown     Artery   
2202      Reg         Lvl    Inside       Gtl      Mitchel     Artery   
2227       IR         Lvl    Inside       Gtl      Edwards       Norm   
2322      Reg         Lvl    Inside       Gtl       IDOTRR       Norm   
2523      Reg         Lvl    Corner       Gtl      Edwards       Norm   
2529      Reg         Lvl    Inside       Gtl      OldTown       Norm   

     BldgType HouseStyle  OverallQual  OverallCond  YearBuilt  YearRemodAdd  \
79       1Fam     1Story            5            5       1920          1950   
109    TwnhsE     1Story            7            5       1998          1998   
404      1Fam       SLvl            6            5       1962          1962   
495      1Fam     1Story            2            4       1940          1950   
558      1Fam     1Story            4            5       1920          1950   
680      1Fam     1.5Fin            5            5       1932          2000   
683    TwnhsE     1Story            7            5       1986          1986   
895      1Fam     1Story            6            6       1958          1958   
1088     1Fam     1.5Fin            4            4       1959          1959   
1346     1Fam     2Story            7            9       1920          1988   
1516     1Fam     2Story            7            5       2003          2004

In [44]:
## Removing these
df = df[~df['Coordinates'].isnull()]

### Let's save our new dataframe to use in Tableau
- will name it "housing.csv"

In [48]:
# create new cleaned .csv file
df.to_csv('housing.csv')